In [8]:
!pip install nglview --user
import nglview as nv
import requests 
import json  
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}
keyword_clause = {
    "type": "terminal",
    "service": "full_text", # где искать - весь текст
    "parameters": {
        "value": "riboflavin" # ключевые слова - рибофлавин
    }
}

my_query["query"]["nodes"].append(keyword_clause)
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.0, #разрешение не хуже 2х ангстрем
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 1, #лигандов должно быть больше одного
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2020-01-01", #дата: с
            "to": "2023-01-01",   #дата: по
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'
json_query = json.dumps(my_query) 
search = requests.post(f'{rcsb}', data=json_query) # Отсылаю запрос


/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [9]:
search #проверка, если код [200], то все хорошо

<Response [200]>

In [10]:
search_result = search.json() # Распаковываю ответ сервера в словарь

In [11]:
best_hit = search_result["result_set"][0] # Лучшая находка по рейтингу поиска
best_hit

{'identifier': '7QF3',
 'score': 0.9921726700971985,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 18312, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 11767, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 25561, 'original_score': 1.0, 'norm_score': 1.0}]},
  {'service_type': 'full_text',
   'nodes': [{'node_id': 11498,
     'original_score': 7.109859466552734,
     'norm_score': 0.9686906803887936}]}]}

далее буду работать с PDB ID 7QF3

Дата поиска была с 2020-01-01 по 2023-01-01, на странице белка указана дата 2022-02-16 - подходит
Разрешение не хуже 2х ангстрем - Resolution: 1.10 Å - подходит
Число лигандов не меньше 2х - Ligands 4 Unique - подходит
Riboflavin-binding proteins for singlet oxygen production. - Заголовок статьи описания белка - подходит, тк содержит ключевое слово "riboflavin"
Белок подходит по всем параметрам, если на сайте rcsb задать необхожимые фильтры поиска, то первый в выдаче как раз 7QF3
Белок miniSOG (7QF3) является фотосенсибилизатором синглетного кислорода, рибофлавин выполняет роль хромофора, необходимого для повышения выхода синглетного кислорода 

In [12]:
from ipywidgets import interact, fixed

In [13]:
representations = [
  'ball+stick',      # шаростержневая модель
  'backbone',        # прямые линии, соединяющие С-альфа атомы
  'cartoon',         # условное отображение вторичной структуры
  'helixorient',     # упрощенное отображение 
  'hyperball',       # сглаженная шаростержневая модель
  'licorice',        # стержневая модель (без шаров)
  'line',            # очень тонкая стержневая модель
  'point',           # атомы в виде плоских точек
  'ribbon',          # отображение остова в виде ленты
  'rocket',          # отображение альфа-спиралей как цилиндров
  'rope',            # отображение остова в виде колбасы
  'spacefill',       # атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса
  'surface',         # поверхность
  'trace',           # сглаженная линия, соединяющая С-альфа атомы
  'tube'             # более сдержанный rope
]
colors = [
  'random',
  'uniform',
  'atomindex',      # от синего к красному с ростом номера атома
  'residueindex',   # от синего к красному с ростом номера остатка
  'chainindex',     # каждой цепи свой цвет
  'sstruc',         # стандартные цвета для типа вторичной структуры
  'element',        # стандартные цвета для химических элементов
  'resname',        # свой цвет каждому из 20 остатков
  'bfactor',        # чем темнее, тем подвижнее
  'hydrophobicity', # чем темнее, тем гидрофобнее
]

In [14]:
my_examples = {
    'Example 3': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры
Показана поверхность, с непрозрачностью 0.1
Лиганды в виде hyperball, покрашены в оттенок желтого на ваш выбор
''',  'representations': [
    {
        'type': 'cartoon',                      
        'params': {
            'sele': 'protein',               
            'color': 'sstruc'  
          }
    },
    {
        'type': 'surface',                      
        'params': { 
            'sele': 'protein',  
            'color':'white',
            'opacity': 0.1
          }
    },
    {
        'type': 'hyperball',                      
        'params': {
            'sele': 'ligand',                     
            'color': 'yellow'  
          }
    }
 ] 
},
 'Example 4': {
        'description': ''' Белок в виде cartoon, покраска по типу вторичной структуры
Боковые радикалы покрашены по элементу, показаны линиями
Боковые радикалы ароматических аминокислот показаны в стержневой модели
Лиганды показаны в виде Ван-дер-Ваальсовых сфер, покрашены по гидрофобности ''' ,
     'representations': [
         {
             'type':'cartoon',                      
        'params': {
            'sele': 'protein',               
            'color': 'sstruc'  
                  }
         },
         {
             'type':'line',
             'params': {
                 'sele':'sidechainAttached',
                 'color':'element'
             }
         },
         {
             'type':'licorice',
            'params': {
                'sele':'aromatic'
            }
         },
         {
             'type': 'spacefill',
             'params': {
                 'sele':'ligand',
                 'color':'hydrophobicity'
             }
         }
     ]
},
     'Example 5': {
        'description': ''' Белок в виде tube, покраска по типу вторичной структуры
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды показаны линиями, покрашены по элементам
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер ''' ,
     'representations': [   
         {
             'type':'tube',
             'params': {
                 'sele':'protein',
                 'color': 'sstruc' 
             }
         },
         {
          'type': 'licorice',
          'params': {
              'sele':'sidechainAttached and not ligand',
              'color':'hydrophobicity'
          }   
         },
         {
             'type':'line',
             'params': {
                  'sele':'ligand',
                  'color':'element'
             }
         },
         {
             'type':'spacefill',
             'params':{
                 'sele':'ion'
             }
         }, 
          {
             'type':'spacefill',
             'params':{
                 'sele':'water'
             }
         }
     ]
 }
              }              


In [15]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("7qf3", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 3', 'Example 4', 'Example 5'), va…

NGLWidget()